In [50]:
import os
import re
import time
import random
import math
import requests
import json
import pandas as pd
from tqdm import tqdm
from datetime import datetime
from dotenv import load_dotenv
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.support.ui import Select
from selenium.common.exceptions import NoSuchElementException
from selenium.webdriver.common.action_chains import ActionChains
from selenium.webdriver.common.desired_capabilities import DesiredCapabilities

In [51]:
# 读取需要的环境变量
load_dotenv()
# link info
SF_URL = os.getenv('SF_URL')
LDTJ_URL = os.getenv('LDTJ_URL')
JBXX_URL = os.getenv('JBXX_URL')
CTD_URL = os.getenv('CTD_URL')
IMG_URL = os.getenv('IMG_URL')
PM_URL = os.getenv('PM_URL')
PM_FC_URL = os.getenv('PM_FC_URL')
DSH_URL = os.getenv('DSH_URL')
YSH_URL = os.getenv('YSH_URL')
DSH_PAGE = os.getenv('DSH_PAGE')
YSH_PAGE = os.getenv('YSH_PAGE')
PAGE_TAIL = os.getenv('PAGE_TAIL')
BASE_NAME = os.getenv('BASE_NAME')

# GJ LINK
CITY_CODE_URL = os.getenv('CITY_CODE_URL')
QCZS_URL = os.getenv('QCZS_URL')
# headers info 
img_headers = {
    "Accept": os.getenv("ACCEPT"),
    "Accept-Encoding": os.getenv("ACCEPT_ENCODING"),
    "Accept-Language": os.getenv("ACCEPT_LANGUAGE"),
    "Authorization": os.getenv("AUTHORIZATION"),
    "Connection": os.getenv("CONNECTION"),
    "Content-Length": os.getenv("CONTENT_LENGTH"),
    "Content-Type": os.getenv("CONTENT_TYPE"),
    "Cookie": os.getenv("COOKIE"),
    "Host": os.getenv("HOST"),
    "origin": os.getenv("ORIGIN"),
    "Referer": os.getenv("REFERER"),
    "Sec-Ch-Ua": os.getenv("SEC_CH_UA"),
    "Sec-Ch-Ua-Mobile": os.getenv("SEC_CH_UA_MOBILE"),
    "Sec-Ch-Ua-Platform": os.getenv("SEC_CH_UA_PLATFORM"),
    "Sec-Fetch-Dest": os.getenv("SEC_FETCH_DEST"),
    "Sec-Fetch-Mode": os.getenv("SEC_FETCH_MODE"),
    "Sec-Fetch-Site": os.getenv("SEC_FETCH_SITE"),
    "User-Agent": os.getenv("USER_AGENT")
}
headers = {
    "Accept": os.getenv("ACCEPT"),
    "Accept-Encoding": os.getenv("ACCEPT_ENCODING"),
    "Accept-Language": os.getenv("ACCEPT_LANGUAGE"),
    "Authorization": os.getenv("AUTHORIZATION"),
    "Connection": os.getenv("CONNECTION"),
    "Cookie": os.getenv("COOKIE"),
    "Host": os.getenv("HOST"),
    "Referer": os.getenv("REFERER"),
    "Sec-Ch-Ua": os.getenv("SEC_CH_UA"),
    "Sec-Ch-Ua-Mobile": os.getenv("SEC_CH_UA_MOBILE"),
    "Sec-Ch-Ua-Platform": os.getenv("SEC_CH_UA_PLATFORM"),
    "Sec-Fetch-Dest": os.getenv("SEC_FETCH_DEST"),
    "Sec-Fetch-Mode": os.getenv("SEC_FETCH_MODE"),
    "Sec-Fetch-Site": os.getenv("SEC_FETCH_SITE"),
    "User-Agent": os.getenv("USER_AGENT")}


In [52]:
### 辅助函数
# 装饰器，如果函数没有返回值，则一直重试
def retry_if_no_return(func):
    def wrapper(*args, **kwargs):
        # 定义重试次数
        retry_times = 5
        while retry_times>=0:
            result = func(*args, **kwargs)
            if result:
                return result
            # 如果函数没有返回值，可以在这里添加日志或等待时间
            time.sleep(2)
            retry_times -= 1
    return wrapper

# 遍历url列表下载图片
@retry_if_no_return
def download_image(url,save_path_name,headers):
    headers = headers
    try:
        r = requests.get(url, headers=headers)
        if r.status_code == 200:
            with open(save_path_name, 'wb') as f:
                f.write(r.content)
                return True
    except:
        return False
    time.sleep(random.random())

In [53]:
# GJ_INFO
# 获取市州、区县编码
def get_city_code(code,headers):
    """获取市州、区县编码"""
    url = CITY_CODE_URL
    # 请求的payload
    params = {
        'code': f'{code}',
    }

    # 发送GET请求
    response = requests.get(url, headers=headers, params=params)
    # 检查响应状态码
    if response.status_code == 200:
        # 解析响应内容
        data = response.json()
        return data
    else:
        print("请求失败，状态码：", response.status_code)
        return False
# 获取基本信息
def get_gj_info_total(code,headers,sjdm=None,ydlb=None,sfsty=None,sfstypxy=None,sfzdbb=None,cylx=None,
                sfjxzcyd=None,sfdbnpyd=None,sfqmpk=None,sfyjd=None,sfgjswy=None,sfsjswy=None,
                sftzy=None,sfttcpyd=None,sfwryxcyd=None,tdlylx=None):
    result_list = []
    """获取基本信息"""
    url = QCZS_URL
    params = {
        'pageNum': 1, # 页码
        'pageSize': 50, # 每页显示数量
        'sjdm': sjdm, # 省市区编码
        'ydlb': ydlb, # 类别
        'sfsty': sfsty, # 水团
        'sfstypxy': sfstypxy, # 水团平行
        'sfzdbb': sfzdbb, # 整段标本
        'cylx': cylx, # 采样类型
        'sfjxzcyd': sfjxzcyd, # 机械组成样点
        'sfdbnpyd': sfdbnpyd, # 地理标志点
        'sfqmpk': sfqmpk, # 全面铺开
        'sfyjd': sfyjd, # 盐碱地
        'sfgjswy': sfgjswy, # 生物点
        'sfsjswy': sfsjswy, # 省级生物点
        'sftzy': sftzy, # 土钻样
        'sfttcpyd': sfttcpyd, # 土特产
        'sfwryxcyd': sfwryxcyd, # xc污染
        'tdlylx': tdlylx, # TD利用类型
        'keyword': '',
        'xzqdm': f'{code}', # 行政区划代码
    }
        # 发送GET请求
    response = requests.get(url, headers=headers, params=params)
    # 检查响应状态码
    if response.status_code == 200:
        # 解析响应内容
        data = response.json()
        total = data['result']['total']
            # 计算有多少页
        page_num = math.ceil(total / 50)
        # 循环获取每一页的编码
        for i in range(1, page_num + 1):
            params['pageNum'] = i
            response = requests.get(url=url, headers=headers, params=params)
            data = response.json()
            result_list += data['result']['records']
        return result_list
    else:
        print("请求失败，状态码：", response.status_code)
        return False



In [54]:
# 获取施肥信息
def get_sf_info(point_id,headers):
    """获取施肥信息"""
    url = f"{SF_URL}{point_id}"
    # 发送GET请求
    response = requests.get(url, headers=headers)
    # 检查响应状态码
    if response.status_code == 200:
        # 解析响应内容
        data = response.json()
        return data
    else:
        print("请求失败，状态码：", response.status_code)
        return False
# 获取图片信息
def get_img_info(point_id,headers):
    """获取图片和视频链接"""
    url = IMG_URL
    # 请求的JSON数据
    # 请根据实际情况替换下面的data字典
    data = {
        "glbh": f"{int(point_id)}"
    }
    # 将字典转换为JSON格式的字符串
    payload = json.dumps(data)
    # 发送POST请求
    response = requests.post(url, headers=headers, data=payload)
    # 检查响应状态码
    if response.status_code == 200:
        # 解析响应内容
        data = response.json()
        return data
    else:
        print("请求失败，状态码：", response.status_code)
        return False
# 获取立地条件信息
def get_ldtj_info(point_id,headers):
    """获取立地条件信息"""
    url = f"{LDTJ_URL}{point_id}"
    # 发送GET请求
    response = requests.get(url, headers=headers)
    # 检查响应状态码
    if response.status_code == 200:
        # 解析响应内容
        data = response.json()
        return data
    else:
        print("请求失败，状态码：", response.status_code)
        return False
# 获取样点基本信息
def get_base_info(point_id,headers):
    """获取基本信息"""
    url = f"{JBXX_URL}{point_id}"
        # 发送GET请求
    response = requests.get(url, headers=headers)
    # 检查响应状态码
    if response.status_code == 200:
        # 解析响应内容
        data = response.json()
        return data
    else:
        print("请求失败，状态码：", response.status_code)
        return False
# 获取采土袋信息
def get_ctd_info(point_id,headers):
    """获取采土袋信息"""
    url = f"{CTD_URL}{point_id}"
    # 发送GET请求
    response = requests.get(url, headers=headers)
    # 检查响应状态码
    if response.status_code == 200:
        # 解析响应内容
        data = response.json()
        return data
    else:
        print("请求失败，状态码：", response.status_code)
        return False
    
# 获取剖面信息
def get_pm_info(point_id,headers):
    """获取剖面信息"""
    url = f"{PM_URL}{point_id}"
    # 发送GET请求
    response = requests.get(url, headers=headers)
    # 检查响应状态码
    if response.status_code == 200:
        # 解析响应内容
        data = response.json()
        return data
    else:
        print("请求失败，状态码：", response.status_code)
        return False
# 获取剖面发生层信息
def get_pmfc_info(point_id,headers):
    """获取剖面发生层信息"""
    url = f"{PM_FC_URL}{point_id}"
    # 发送GET请求
    response = requests.get(url, headers=headers)
    # 检查响应状态码
    if response.status_code == 200:
        # 解析响应内容
        data = response.json()
        return data
    else:
        print("请求失败，状态码：", response.status_code)
        return False
# 获取当前页面cookie信息
def get_cookie():
    """获取当前页面cookie信息"""
    # 使用JavaScript获取Cookie
    cookie_script = """
    return document.cookie;
    """
    cookie_value = driver.execute_script(cookie_script)
    return cookie_value
# 更新cookie信息
def update_cookie(headers):
    """更新cookie信息"""
    # 获取当前页面cookie信息
    cookie_value = get_cookie()
    # 更新headers
    headers.update({"Cookie": cookie_value})
    return headers
# 获取已审核数量
def get_audit_num(headers):
    """获取已审核数量"""
    url = YSH_URL
    # 发送GET请求
    response = requests.get(url, headers=headers)
    # 检查响应状态码
    if response.status_code == 200:
        # 解析响应内容
        data = response.json()
        return data['result']
    else:
        print("请求失败，状态码：", response.status_code)
        return False
# 获取待审核数量
def get_wait_num(headers):
    """获取待审核数量"""
    url = DSH_URL
    # 发送GET请求
    response = requests.get(url, headers=headers)
    # 检查响应状态码
    if response.status_code == 200:
        # 解析响应内容
        data = response.json()
        return data['result']
    else:
        print("请求失败，状态码：", response.status_code)
        return False
# 获取指定页面的编码
def get_set_page_num(url,headers):
    """获取指定页面的编码"""
    response = requests.get(url, headers=headers)
    # 检查响应状态码
    if response.status_code == 200:
        # 解析响应内容
        data = response.json()
        info_list = data['result']['records']
        # 循环获取编码
        temp_dict = [{_['ydbh']:_['ydlb']} for _ in info_list]
        return temp_dict
    else:
        print("请求失败，状态码：", response.status_code)
        return False

# 获取已审核的编码
def get_page_number(total,headers):
    """获取当前传入页面的编码,默认每一页50"""
    # 计算有多少页
    page_num = math.ceil(total / 50)
    # 循环获取每一页的编码
    result_list = []
    for i in range(1, page_num + 1):
        url = f"{YSH_PAGE}{i}{PAGE_TAIL}"
        result_list+=get_set_page_num(url,headers)
        time.sleep(random.random())
    return result_list

# 获取待审核的编码
def get_wait_page_number(total,headers):
    """获取当前传入页面的编码,默认每一页50"""
    # 计算有多少页
    page_num = math.ceil(total / 50)
    # 循环获取每一页的编码
    temp_list = []
    for i in range(1, page_num + 1):
        url = f"{DSH_PAGE}{i}{PAGE_TAIL}"
        temp_list+=get_set_page_num(url,headers)
        time.sleep(random.random())
    return temp_list
    
# 随机休眠
def random_sleep():
    """随机休眠"""
    time.sleep(random.random())
    return
# 获取当天日期
def get_today_date():
    """获取当天日期"""
    today = datetime.today()
    return today.strftime("%Y%m%d")

In [55]:
# 配置浏览器
# chrome.exe --remote-debugging-port=9999 --user-data-dir="D:\Selenium\AutomationProfile"
# chrome.exe --remote-debugging-port=9999 --user-data-dir="D:\Program Files\ChromeDir"
options = webdriver.ChromeOptions()
options.add_experimental_option("debuggerAddress", "localhost:9998")
driver = webdriver.Chrome(options=options)

driver.implicitly_wait(60)

In [56]:
# 保存路径
save_path = r"F:\collection_spb_info\GJ\QXG"
# 如果没有该文件夹，则创建
if not os.path.exists(save_path):
    os.makedirs(save_path)

# 检查heraders并更新

In [57]:

headers = update_cookie(headers)

In [ ]:
headers

In [49]:
# 查看区县编码
get_city_code(5205,headers)

{'success': True,
 'message': None,
 'code': 200,
 'result': [{'ctime': None,
   'utime': None,
   'id': '3338',
   'parentId': '1032',
   'code': '520502',
   'name': '七星关区',
   'fullname': None,
   'level': 3,
   'centerx': 105.284852,
   'centery': 27.302085,
   'sfspsdx': None,
   'sfqmpk': '1'},
  {'ctime': None,
   'utime': None,
   'id': '3339',
   'parentId': '1032',
   'code': '520521',
   'name': '大方县',
   'fullname': None,
   'level': 3,
   'centerx': 105.609254,
   'centery': 27.143521,
   'sfspsdx': None,
   'sfqmpk': '1'},
  {'ctime': None,
   'utime': None,
   'id': '3341',
   'parentId': '1032',
   'code': '520523',
   'name': '金沙县',
   'fullname': None,
   'level': 3,
   'centerx': 106.222103,
   'centery': 27.459693,
   'sfspsdx': None,
   'sfqmpk': '1'},
  {'ctime': None,
   'utime': None,
   'id': '3342',
   'parentId': '1032',
   'code': '520524',
   'name': '织金县',
   'fullname': None,
   'level': 3,
   'centerx': 105.768997,
   'centery': 26.668497,
   'sfspsdx': 

In [59]:
# 获取选择条件的编码
# 更新headers
headers = update_cookie(headers=headers)
# get info 
info_list = get_gj_info_total(code=520502,headers=headers)


In [60]:
# 保存基本信息
df_base_info =pd.DataFrame(info_list)
df_base_info.to_excel(os.path.join(save_path,f'base_info_{get_today_date()}_{len(info_list)}.xlsx'),index=False)


In [61]:
df_base_info.head(1)

ctime                utime  \
0  2023-08-04 17:36:57  2024-07-20 18:10:42   

                                     id   bsm  ysdm              ydbh ydlb  \
0  e727e242-cdb2-4f8a-85d0-a5e0ababa5f8  None  None  5205020101000104    0   

         zldwdm zldwmc       xzdm  ... gjjshsj    bz  sfspsdx  sfqmpk  \
0  520502123202    向阳村  520502123  ...    None  None        0       1   

   gjlycjCy  zdbbzt  appVersion  sfwryxcyd  sfwrxcyd2 sfgd  
0      None    None        None          0          0    0  

[1 rows x 91 columns]

In [62]:
# 区分样点类别
pm_list = df_base_info[df_base_info['ydlb']=='1']['ydbh'].to_list()
bc_list = df_base_info[df_base_info['ydlb']=='0']['ydbh'].to_list()
# 分类型打印样点信息
print(f"剖面样点数：{len(pm_list)}",f"表层样点数：{len(bc_list)}")
# 检查总数
df_base_info.shape[0]==len(pm_list)+len(bc_list)

剖面样点数：44 表层样点数：2695


True

In [63]:
# 更新替换信息
loop_all_point = bc_list+pm_list

In [64]:
# 测试一个点位的图片信息
img_info = get_img_info(loop_all_point[0],img_headers)
img_info

{'success': True,
 'message': None,
 'code': 200,
 'result': [{'ctime': '2023-11-03 14:18:37',
   'utime': '2023-11-03 14:18:37',
   'id': '1720324584530612225',
   'glbh': '5205020101000104',
   'wjbh': None,
   'wjmc': '1698990601498.mp4',
   'wjlx': None,
   'wjfl': '1400',
   'wjlj': 'ssp-dccy/2023-11-03/520502/e8068222-2979-4413-86e0-c644d24ce47f.mp4',
   'jd': 105.465458,
   'wd': 27.495498,
   'jdu': None,
   'cjsj': '2023-11-03 13:50:22',
   'bz': None,
   'url': None,
   'rawUrl': None},
  {'ctime': '2023-11-03 14:18:37',
   'utime': '2023-11-03 14:18:37',
   'id': '1720324584530612226',
   'glbh': '5205020101000104',
   'wjbh': None,
   'wjmc': None,
   'wjlx': None,
   'wjfl': '1300',
   'wjlj': 'ssp-dccy/2023-11-03/520502/20b627d2-0fcf-44ae-9587-4cd819b36bb4.jpg',
   'jd': 105.465455,
   'wd': 27.495483,
   'jdu': None,
   'cjsj': '2023-11-03 13:41:47',
   'bz': None,
   'url': None,
   'rawUrl': None},
  {'ctime': '2023-11-03 14:18:37',
   'utime': '2023-11-03 14:18:37',
 

In [65]:
# 获取图片链接信息
# 更新headers
img_headers = update_cookie(img_headers)
img_info_list = []
for one_point in tqdm(loop_all_point):
    one_point_img_info = get_img_info(one_point,img_headers)['result']
    # 为链接增加域名
    prefix = BASE_NAME
    updated_list = [{**item, 'wjlj': f"{prefix}{item['wjlj']}"} for item in one_point_img_info]
    # 随机休眠
    # time.sleep(random.random())
    img_info_list+=updated_list

100%|██████████| 2739/2739 [08:19<00:00,  5.48it/s] 


In [66]:
df_img_info = pd.DataFrame(img_info_list)
df_img_info.head(1)

ctime                utime                   id  \
0  2023-11-03 14:18:37  2023-11-03 14:18:37  1720324584530612225   

               glbh  wjbh               wjmc  wjlx  wjfl  \
0  5205020101000104  None  1698990601498.mp4  None  1400   

                                                wjlj          jd         wd  \
0  https://sanpu.iarrp.cn/ssp-dccy/2023-11-03/520...  105.465458  27.495498   

   jdu                 cjsj    bz   url rawUrl  
0  NaN  2023-11-03 13:50:22  None  None   None

In [67]:
# 保存媒体信息
df_img_info.to_excel(os.path.join(save_path, f'img_info_{get_today_date()}_{len(loop_all_point)}.xlsx'), index=False)


In [68]:
# 测试一个点位的立地调查信息
ldtj_info = get_ldtj_info(loop_all_point[0],headers)
ldtj_info

{'success': True,
 'message': None,
 'code': 200,
 'result': {'ctime': '2023-11-03 14:18:37',
  'utime': '2023-11-03 14:43:53',
  'id': '1720324584509640705',
  'ydbh': '5205020101000104',
  'zldwmc': '向阳村',
  'cyjd': 105.46566368521452,
  'cywd': 27.495411672381653,
  'hbgd': 1248.0,
  'cysj': '2023-11-03 14:16:34',
  'tqqk': '03',
  'dcz': '王朴',
  'dcdw': '航天宏图信息技术股份有限公司',
  'qslx': 'W',
  'qscd': 'S',
  'jyclfd': 'N',
  'jycljj': None,
  'dblsfd': 'N',
  'dblsdx': None,
  'dbybfd': 'N',
  'dbybhd': None,
  'dblxkd': None,
  'dblxcd': None,
  'dblxfd': 'N',
  'dblxjj': None,
  'dblxsl': None,
  'trsh': '0',
  'ddx': 'MO',
  'zdx': 'MM',
  'xdx': 'SL',
  'dxbw': 'BOf',
  'dxbwqt': None,
  'pd': 'II',
  'px': 'NW',
  'pxn': '02',
  'my': '27',
  'myqt': None,
  'mz': 'VA',
  'mzqt': None,
  'zblx': '11',
  'zbzwysz': '农作物',
  'zbfgd': None,
  'zbqmfgd': None,
  'zbgmfgd': None,
  'zbcbfgd': None,
  'tdlylx': '0101',
  'tdlylxqt': None,
  'tdlylxbg': '[]',
  'sftsncp': '0',
  'tsncpzwlx

In [69]:
# 获取立地条件信息
# 更新headers
headers = update_cookie(headers)
ldtj_info_list = []
for one_point in tqdm(loop_all_point):
    one_point_ldtj_info = get_ldtj_info(one_point,headers)['result']
    ldtj_info_list.append(one_point_ldtj_info)
    # 随机休眠
    # time.sleep(random.random())

100%|██████████| 2739/2739 [08:55<00:00,  5.11it/s] 


In [70]:
ldtj_info_list,len(ldtj_info_list)

([{'ctime': '2023-11-03 14:18:37',
   'utime': '2023-11-03 14:43:53',
   'id': '1720324584509640705',
   'ydbh': '5205020101000104',
   'zldwmc': '向阳村',
   'cyjd': 105.46566368521452,
   'cywd': 27.495411672381653,
   'hbgd': 1248.0,
   'cysj': '2023-11-03 14:16:34',
   'tqqk': '03',
   'dcz': '王朴',
   'dcdw': '航天宏图信息技术股份有限公司',
   'qslx': 'W',
   'qscd': 'S',
   'jyclfd': 'N',
   'jycljj': None,
   'dblsfd': 'N',
   'dblsdx': None,
   'dbybfd': 'N',
   'dbybhd': None,
   'dblxkd': None,
   'dblxcd': None,
   'dblxfd': 'N',
   'dblxjj': None,
   'dblxsl': None,
   'trsh': '0',
   'ddx': 'MO',
   'zdx': 'MM',
   'xdx': 'SL',
   'dxbw': 'BOf',
   'dxbwqt': None,
   'pd': 'II',
   'px': 'NW',
   'pxn': '02',
   'my': '27',
   'myqt': None,
   'mz': 'VA',
   'mzqt': None,
   'zblx': '11',
   'zbzwysz': '农作物',
   'zbfgd': None,
   'zbqmfgd': None,
   'zbgmfgd': None,
   'zbcbfgd': None,
   'tdlylx': '0101',
   'tdlylxqt': None,
   'tdlylxbg': '[]',
   'sftsncp': '0',
   'tsncpzwlx': None,
  

In [71]:
df_ldtj_info = pd.DataFrame(ldtj_info_list)
df_ldtj_info.head(1)

ctime                utime                   id  \
0  2023-11-03 14:18:37  2023-11-03 14:43:53  1720324584509640705   

               ydbh zldwmc        cyjd       cywd    hbgd  \
0  5205020101000104    向阳村  105.465664  27.495412  1248.0   

                  cysj tqqk  ... glswylszl rzlstjzb hlsbctrhhfd hlsbctrhhzl  \
0  2023-11-03 14:16:34   03  ...      None     None           4         200   

  cyhydgs cbfmc             cbfzjhm      cbflxfs hydgs  \
0    None   陈能奎  522401197310035633  13985879507   5.0   

                                                  bz  
0  经稀盐酸测试，无明显石灰反应现象。经核实水田已翻耕，未施肥，可以采样。容重样品在未翻耕的边缘...  

[1 rows x 131 columns]

In [ ]:
# 过滤NONE值
ldtj_info_list = [x for x in ldtj_info_list if x is not None]  # 过滤掉 None 值
df_ldtj_info = pd.DataFrame(ldtj_info_list)
df_ldtj_info.head(1)


In [72]:
# 保存立地条件信息
df_ldtj_info.to_excel(os.path.join(save_path,f'ldtj_info_{get_today_date()}_{len(loop_all_point)}.xlsx'),index=False)

In [73]:
# 测试一个点位的采土袋信息
ctd_info = get_ctd_info(loop_all_point[0],headers)
ctd_info

{'success': True,
 'message': None,
 'code': 200,
 'result': [{'ctime': '2023-11-03 14:18:37',
   'utime': '2023-11-25 11:17:48',
   'id': '1720324584513835013',
   'ctdbh': '520502010100010410',
   'ydbh': '5205020101000104',
   'ydlb': '0',
   'cylx': '1',
   'yplx': '1',
   'fscxh': None,
   'ypzl': 6785.0,
   'jszt': '2',
   'jshzt': '2'},
  {'ctime': '2023-11-03 14:18:37',
   'utime': '2023-11-03 14:18:37',
   'id': '1720324584518029313',
   'ctdbh': '520502010100010420',
   'ydbh': '5205020101000104',
   'ydlb': '0',
   'cylx': '1',
   'yplx': '4',
   'fscxh': None,
   'ypzl': None,
   'jszt': '1',
   'jshzt': None}],
 'timestamp': 1723790166440,
 'elapse': 0}

In [74]:
# 获取采土袋信息
# 更新headers
headers = update_cookie(headers)
ctd_info_list = []
for one_point in tqdm(loop_all_point):
    one_point_ctd_info = get_ctd_info(one_point,headers)['result']
    ctd_info_list+=one_point_ctd_info
    # 随机休眠
    # time.sleep(random.random())

100%|██████████| 2739/2739 [09:15<00:00,  4.93it/s]  


In [75]:
df_ctd_info = pd.DataFrame(ctd_info_list)
df_ctd_info.head(1)

ctime                utime                   id  \
0  2023-11-03 14:18:37  2023-11-25 11:17:48  1720324584513835013   

                ctdbh              ydbh ydlb cylx yplx  fscxh    ypzl jszt  \
0  520502010100010410  5205020101000104    0    1    1    NaN  6785.0    2   

  jshzt  
0     2

In [76]:
# 保存采土袋信息
df_ctd_info.to_excel(os.path.join(save_path, f'ctd_info_{get_today_date()}_{len(loop_all_point)}.xlsx'), index=False)

In [77]:
# 测试一个点位的施肥信息
sf_info = get_sf_info(loop_all_point[0],headers)
sf_info

{'success': True,
 'message': None,
 'code': 200,
 'result': [{'ctime': '2023-11-03 14:18:37',
   'utime': '2023-11-03 14:18:37',
   'id': '1720324584513835010',
   'ydbh': '5205020101000104',
   'jd': '第二季',
   'fllx': '化学氮肥',
   'flmc': '三元复合（混）肥',
   'swyl': 30.0,
   'hlzb': 15,
   'yshl': 4.5,
   'zwlx': '01',
   'zwlxqt': None,
   'jfzb': 70,
   'zfzb': 30},
  {'ctime': '2023-11-03 14:18:37',
   'utime': '2023-11-03 14:18:37',
   'id': '1720324584513835011',
   'ydbh': '5205020101000104',
   'jd': '第二季',
   'fllx': '磷肥',
   'flmc': '三元复合（混）肥',
   'swyl': 30.0,
   'hlzb': 15,
   'yshl': 4.5,
   'zwlx': '01',
   'zwlxqt': None,
   'jfzb': 70,
   'zfzb': 30},
  {'ctime': '2023-11-03 14:18:37',
   'utime': '2023-11-03 14:18:37',
   'id': '1720324584513835012',
   'ydbh': '5205020101000104',
   'jd': '第二季',
   'fllx': '钾肥',
   'flmc': '三元复合（混）肥',
   'swyl': 30.0,
   'hlzb': 15,
   'yshl': 4.5,
   'zwlx': '01',
   'zwlxqt': None,
   'jfzb': 70,
   'zfzb': 30}],
 'timestamp': 17237907236

In [78]:
# 获取施肥信息
# 更新headers
headers = update_cookie(headers)
sf_info_list = []
for one_point in tqdm(loop_all_point):
    one_point_sf_info = get_sf_info(one_point,headers)['result']
    sf_info_list+=one_point_sf_info
    # 随机休眠
    # time.sleep(random.random())

100%|██████████| 2739/2739 [09:56<00:00,  4.59it/s]  


In [79]:
df_sf_info = pd.DataFrame(sf_info_list)
df_sf_info.head(1)

ctime                utime                   id  \
0  2023-11-03 14:18:37  2023-11-03 14:18:37  1720324584513835010   

               ydbh   jd  fllx      flmc  swyl  hlzb  yshl zwlx zwlxqt  jfzb  \
0  5205020101000104  第二季  化学氮肥  三元复合（混）肥  30.0  15.0   4.5   01   None  70.0   

   zfzb  
0  30.0

In [80]:
# 保存施肥信息
df_sf_info.to_excel(os.path.join(save_path, f'sf_info_{get_today_date()}_{len(loop_all_point)}.xlsx'), index=False)

# 剖面信息

In [81]:
pm_point_id = pm_list

In [82]:
# 测试剖面点位的信息
pm_info = get_pm_info(pm_point_id[0],headers)
pm_info

{'success': True,
 'message': None,
 'code': 200,
 'result': {'ctime': '2024-01-28 20:55:26',
  'utime': '2024-01-29 16:59:11',
  'id': '1751589802187264001',
  'ydbh': '5205020101100004',
  'pmzp': None,
  'yxtchd': 120,
  'gzchd': 15.0,
  'tthd': 120,
  'ttgx': None,
  'ttgxqt': None,
  'fscs': 5,
  'fsxjs': '剖面点位于地下水位高，排水不畅的洼地区域，地势平坦，过去长期积水，地下水位较高、水分饱和，导致土壤中的氧气缺乏，形成了还原环境，高价铁锰化合物还原成低价铁锰化合物，颜色呈蓝绿色或青灰色的潜育层，土块分散成糊状。表层土经耕作，团粒结构发育，土质疏松。剖面下部土体经常为水浸泡，具有明显的有机质累积作用及潜育化作用，致使剖面层次分化不太明显。',
  'scxnps': '剖面中的有机质含量较高，具有较好的肥力，水分条件较好，更有利于作物吸收养分，具有较高的生产性能，能够为水稻等作物提供充足的养分。但由于地处低洼地区，地形较低，容易发生渍水。',
  'zjzxyj': '基本符合',
  'fsxtg': '人为土',
  'fsxyg': '人为水成土',
  'fsxtl': '水稻土',
  'fsxyl': '潜育水稻土',
  'fsxts': '青灰泥田',
  'fsxtz': '青石灰泥田',
  'xtfltg': '人为土',
  'xtflyg': '水耕人为土',
  'xtfltl': '潜育水耕人为土',
  'xtflyl': '普通潜育水耕人为土',
  'sfydxscx': '0',
  'dxscxsd': None,
  'tbcd': None,
  'tbjhwzw': None,
  'tbjhwzp': None,
  'tkd1jd': 105.2872283,
  'tkd1wd': 27.1743867,
  'tkd2jd': 105.2860183,
  'tkd2wd': 27.1805133,


In [83]:
# 获取剖面信息
# 更新headers
headers = update_cookie(headers)
pm_info_list = []
for one_point in tqdm(pm_point_id):
    one_point_pm_info = get_pm_info(one_point,headers)['result']
    pm_info_list.append(one_point_pm_info)
    # 随机休眠
    time.sleep(random.random())

100%|██████████| 44/44 [00:30<00:00,  1.46it/s]


In [84]:
df_pm_info = pd.DataFrame(pm_info_list)
df_pm_info.head(1)

ctime                utime                   id  \
0  2024-01-28 20:55:26  2024-01-29 16:59:11  1751589802187264001   

               ydbh  pmzp  yxtchd  gzchd  tthd  ttgx ttgxqt  ...     tkd2wd  \
0  5205020101100004  None     120   15.0   120  None   None  ...  27.180513   

       tkd3jd     tkd3wd tkd4jd tkd4wd tkd5jd tkd5wd tkd6jd tkd6wd    bz  
0  105.290658  27.181145   None   None   None   None   None   None  None  

[1 rows x 42 columns]

In [85]:
# 过滤NONE值
pm_info_list = [x for x in pm_info_list if x is not None]  # 过滤掉 None 值
df_pm_info = pd.DataFrame(pm_info_list)
df_pm_info.head(1)


ctime                utime                   id  \
0  2024-01-28 20:55:26  2024-01-29 16:59:11  1751589802187264001   

               ydbh  pmzp  yxtchd  gzchd  tthd  ttgx ttgxqt  ...     tkd2wd  \
0  5205020101100004  None     120   15.0   120  None   None  ...  27.180513   

       tkd3jd     tkd3wd tkd4jd tkd4wd tkd5jd tkd5wd tkd6jd tkd6wd    bz  
0  105.290658  27.181145   None   None   None   None   None   None  None  

[1 rows x 42 columns]

In [86]:
# 保存剖面信息
df_pm_info.to_excel(os.path.join(save_path, f'pm_info_{get_today_date()}_{len(pm_point_id)}.xlsx'), index=False)

In [87]:
# 测试剖面点位发生层信息
pm_fc_info = get_pmfc_info(pm_point_id[0],headers)
pm_fc_info

{'success': True,
 'message': None,
 'code': 200,
 'result': [{'ctime': '2024-01-28 20:55:26',
   'utime': '2024-01-29 17:05:50',
   'id': '1751589802191458305',
   'ydbh': '5205020101100004',
   'xh': 5,
   'fschdsj': 80,
   'fschdxj': 120,
   'fscmc': '潜育层',
   'fscfh': 'Bg3',
   'bjmxd': 'G',
   'bjgdxz': 'W',
   'spywrtbs': '1',
   'ywrtsd': 'N',
   'ywrtmd': 6,
   'ywrtcd': 1,
   'sngtsd': None,
   'sngtmd': None,
   'sngtcd': None,
   'rtbssd': None,
   'rtbsmd': None,
   'rtbscd': None,
   'gxfd': 'N',
   'gxcx': None,
   'gxxz': None,
   'zd': '5',
   'jgxz': 'N',
   'jgdx': 'MAFS',
   'jgdxqt': None,
   'jgfycd': 'WE',
   'tnlsfd': '0',
   'tnlsdx': None,
   'tnlsxz': None,
   'tnlsfhcd': None,
   'tnlszl': 0.0,
   'jcx': '3',
   'bwfd': 'N',
   'bwdx': None,
   'bwwz': None,
   'bwzcwz': None,
   'bwzcwzqt': None,
   'jmfd': 'N',
   'jmwz': None,
   'jmzcwz': None,
   'jmzcwzqt': None,
   'jmytrjzdbd': None,
   'kzlzjhfd': 'N',
   'kzlzjhzl': None,
   'kzlzjhdx': None,
   'kz

In [88]:
# 获取剖面发生层信息
# 更新headers
headers = update_cookie(headers)
pm_fc_info_list = []
for one_point in tqdm(pm_point_id):
    one_point_pm_fc_info = get_pmfc_info(one_point,headers)['result']
    pm_fc_info_list+=one_point_pm_fc_info
    # 随机休眠
    time.sleep(random.random())

100%|██████████| 44/44 [00:29<00:00,  1.48it/s]


In [89]:
df_pm_fc_info = pd.DataFrame(pm_fc_info_list)
df_pm_fc_info.head(1)

ctime                utime                   id  \
0  2024-01-28 20:55:26  2024-01-29 17:05:50  1751589802191458305   

               ydbh  xh  fschdsj  fschdxj fscmc fscfh bjmxd  ... trdwyxqk  \
0  5205020101100004   5       80      120   潜育层   Bg3     G  ...     None   

  shfy ytfy  jhfy  trsjfy glscytrtj glsywlstj glswylszl rzlstjzb    bz  
0    N    N     N      AL      None      None      None     None  None  

[1 rows x 73 columns]

In [90]:
# 过滤NONE值
pm_fc_info_list = [x for x in pm_fc_info_list if x is not None]  # 过滤掉 None 值
df_pm_fc_info = pd.DataFrame(pm_info_list)
df_pm_fc_info.head(1)


ctime                utime                   id  \
0  2024-01-28 20:55:26  2024-01-29 16:59:11  1751589802187264001   

               ydbh  pmzp  yxtchd  gzchd  tthd  ttgx ttgxqt  ...     tkd2wd  \
0  5205020101100004  None     120   15.0   120  None   None  ...  27.180513   

       tkd3jd     tkd3wd tkd4jd tkd4wd tkd5jd tkd5wd tkd6jd tkd6wd    bz  
0  105.290658  27.181145   None   None   None   None   None   None  None  

[1 rows x 42 columns]

In [91]:
# 保存剖面发生层信息
df_pm_fc_info.to_excel(os.path.join(save_path, f'pm_fc_info_{get_today_date()}_{len(pm_point_id)}.xlsx'), index=False)